# 导包

In [1]:
import torch
import torch.nn as nn
import torch.utils.data as Data
import torch.nn.functional as F
import torch.optim as optim
import numpy as np
import random
import os
from Bio import SeqIO
import collections
from tqdm.notebook import tqdm 
from tensorboardX import SummaryWriter

# 初始化类

In [2]:
class intialization():
    def __init__(self, seed_id, iscolab, file_name, windows_size, batch_size,
                 embed_size, class_num, filter_num, filter_size, topk, dropout):
        self.seed_id = seed_id
        self.ISCOLAB = iscolab
        self.FILE = file_name
        self.CONCERN_TAIL = False
        self.WINDOWS_SIZE = windows_size
        self.USE_CUDA = torch.cuda.is_available()
        self.BATCH_SIZE = batch_size
        self.VOCAB_SIZE = 0
        self.embed_size = embed_size
        self.class_num = class_num
        self.filter_num = filter_num
        self.filter_size = filter_size
        self.stride = 1
        self.topk = topk
        self.chanel_num = 1
        self.class_num = 2
        self.dropout = dropout
        self.device = torch.device('cuda' if self.USE_CUDA else 'cpu')
    def set_seed(self):
        """ Set all seeds to make results reproducible """
        torch.manual_seed(self.seed_id)
        torch.cuda.manual_seed_all(self.seed_id)
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False
        np.random.seed(self.seed_id)
        random.seed(self.seed_id)
        os.environ['PYTHONHASHSEED'] = str(self.seed_id)

In [3]:
init = intialization(seed_id=1, iscolab=True, file_name='DNase', windows_size=2, 
                     batch_size=32, embed_size=32, class_num=2, filter_num=16,
                    filter_size=[3,4,5],topk=5, dropout=0.5)

In [4]:
init.set_seed()

# IO读取类

In [5]:
class IO():
    def __init__(self, dir_path, **file_name):
        self.seq_all = []
        self.seq_0 = [] 
        self.seq_1 = []
        self.path_0 = os.path.join(dir_path , file_name['neg'])
        self.path_1 = os.path.join(dir_path , file_name['pos'])
    def get_seq_from_file(self):
        for seq_record in SeqIO.parse(self.path_0,'fasta'):
            self.seq_0.append(seq_record.seq)
        for seq_record in SeqIO.parse(self.path_1,'fasta'):
            self.seq_1.append(seq_record.seq)

        return self.seq_0,self.seq_1 
    def counter(self):
        self.seq_all.extend([self.seq_0[i][j] for i in range(len(self.seq_0)) for j in range(len(self.seq_0[i]))])
        self.seq_all.extend([self.seq_1[i][j] for i in range(len(self.seq_1)) for j in range(len(self.seq_1[i]))])
        counter = collections.Counter(self.seq_all)
        return counter
        

In [6]:
io = IO(dir_path='pred/Dnase',neg='non_DNase_737.txt',pos='DNase_280.txt')

In [7]:
seq0,seq1 = io.get_seq_from_file()

In [8]:
len(seq0),len(seq1)

(737, 280)

In [9]:
io.counter()

Counter({'G': 57431,
         'C': 56910,
         'T': 53503,
         'A': 54571,
         'c': 5988,
         'a': 6354,
         't': 6466,
         'g': 5519})

# Tokenizer类

In [10]:
class tokenizer():
    def __init__(self):
        self.windows_size = init.WINDOWS_SIZE
        self.rna_dict,self.dict_size = self.get_rna_dict()
    
    @staticmethod  
    def __get_all_word(windows_size):
        '''获取所有长度为windows_size的可重复组合'''
        from functools import reduce
        a, b = ['A','C','T', 'G'], windows_size  # 4种字符，匹配5种字符
        res = reduce(lambda x, y:[z0 + z1 for z0 in x for z1 in y], [a] * b)
        return res    
    
    def get_rna_dict(self):
        '''构建字典'''
        rna_dict = {'<PAD>':0,'<UNK>':1}
        num = len(rna_dict)
        for j in range(self.windows_size,0,-1):
            for word in tokenizer.__get_all_word(j):
                rna_dict[word] = num
                num += 1
        return rna_dict,len(rna_dict)
    @staticmethod
    def pad_code(ngram_encode):
        ngram_encode2 = np.zeros([len(ngram_encode),len(max(ngram_encode,key = lambda x: len(x)))]) # 生成样本数*最长序列长度
        for i,j in enumerate(ngram_encode):
            ngram_encode2[i][0:len(j)] = j
        return ngram_encode2
    def encode(self,rna_seq,padding=True,return_pt=True):
        mRNA_dic,_ = self.get_rna_dict()
        init.VOCAB_SIZE = len(mRNA_dic)
        n_gram = [] # 存储基因词
        n_gram_encode = [] # 存储基因词的encode
        n_gram_len = [] # 存储基因链长度
        len_rna_seq = len(rna_seq)
        for i in range(len_rna_seq):
            cur_rna_seq = []
            cur_rna_encode = []
            for j in range(len(rna_seq[i])):
                len_win = len(rna_seq[i][j:j+init.WINDOWS_SIZE])
                if  len_win == init.WINDOWS_SIZE:    
                    cur_rna_seq.append(rna_seq[i][j:j+init.WINDOWS_SIZE].upper())
                    cur_rna_encode.append(mRNA_dic[rna_seq[i][j:j+init.WINDOWS_SIZE].upper()])
            n_gram.append(cur_rna_seq)
            n_gram_encode.append(cur_rna_encode)
            n_gram_len.append(len(cur_rna_encode))
        if padding:
            n_gram_encode = tokenizer.pad_code(n_gram_encode)
        if return_pt:
            n_gram_encode = torch.LongTensor(n_gram_encode)
                
        return n_gram, n_gram_encode, n_gram_len

In [11]:
init.VOCAB_SIZE

0

In [12]:
tokenize = tokenizer()

In [13]:
_, n_gram_encode_0, _ = tokenize.encode(seq0)
_, n_gram_encode_1, _ = tokenize.encode(seq1)

In [14]:
n_gram_encode_all = torch.cat((n_gram_encode_0,n_gram_encode_1),dim=0)

In [15]:
label = torch.cat((torch.zeros(n_gram_encode_0.size(0)).long(),torch.ones(n_gram_encode_1.size(0)).long()),-1)

# Dataset类

In [16]:
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self, seq, label):
        self.seq = seq
        self.label = label
    def __len__(self):
        return len(self.seq)
    def __getitem__(self,idx):
        return self.seq[idx],self.label[idx]
        

In [17]:
customdataset = CustomDataset(n_gram_encode_all,label)

In [18]:
dataloader = torch.utils.data.DataLoader(customdataset,batch_size=init.BATCH_SIZE,shuffle=True)

# Model类

In [19]:
class textCNN2(nn.Module):
        def __init__(self):
            super(textCNN2, self).__init__()
            Vocab = init.VOCAB_SIZE ## 已知词的数量
            Dim = init.embed_size ##每个词向量长度
            Cla = init.class_num ##类别数
            Ci = init.chanel_num ##输入的channel数
            Knum = init.filter_num ## 每种卷积核的数量
            Ks = init.filter_size ## 卷积核list，形如[2,3,4]
            strider = init.stride
            self.topk = init.topk

            self.embed = nn.Embedding(Vocab,Dim,padding_idx=0) ## 词向量，这里直接随机

            self.convs = nn.ModuleList([nn.Conv2d(Ci,Knum,(K,Dim),stride=strider) for K in Ks]) ## 卷积层
            self.dropout = nn.Dropout(init.dropout) 
            self.fc = nn.Linear(len(Ks)*Knum*self.topk,Cla) ##全连接层
        @staticmethod
        def kmax_pooling(x, dim, k):    
            index = x.topk(k, dim=dim)[1].sort(dim=dim)[0]
            return x.gather(dim, index)

        def forward(self,x):
            batch_size = x.shape[0]
            x = self.embed(x) #(N,W,D) (batch_size, 序列长， 嵌入维度)

            x = x.unsqueeze(1) #(N,Ci,W,D) （batch_size, 1, 序列长， 嵌入维度）
            x = [F.relu(conv(x)).squeeze(3) for conv in self.convs] # len(Ks)*(N,Knum,W) 窗口种数*（batch_size, filter数, 序列长）
            x = [textCNN2.kmax_pooling(line,2,self.topk) for line in x]  # len(Ks)*(N,Knum) 窗口种数*（batch_size, filter数, 6）
    #         print([i.shape for i in x])
            x = [line.view(batch_size,-1) for line in x] #len(Ks)*(N,Knum*6)窗口种数*（batch_size*6）
    #         print([i.shape for i in x])
            x = torch.cat(x,1)
    #         print('-------------------')
    #         print([i.shape for i in x])
            x = self.dropout(x)
            logit = self.fc(x)
            return logit

In [20]:
model = textCNN2()

In [21]:
model

textCNN2(
  (embed): Embedding(22, 32, padding_idx=0)
  (convs): ModuleList(
    (0): Conv2d(1, 16, kernel_size=(3, 32), stride=(1, 1))
    (1): Conv2d(1, 16, kernel_size=(4, 32), stride=(1, 1))
    (2): Conv2d(1, 16, kernel_size=(5, 32), stride=(1, 1))
  )
  (dropout): Dropout(p=0.5, inplace=False)
  (fc): Linear(in_features=240, out_features=2, bias=True)
)

# Trainer类

In [22]:
class trainer():
    def __init__(self,model,  epochs, data_x, data_y):
        self.model = model.to(init.device)
        self.data_x = data_x
        self.data_y = data_y
        self.epochs = epochs
        self.len_train = None
        self.len_eval = None
        self.best_evalscore = 0
        self.kfold = 5
        self.k = 0
        self.log_evalacc = torch.empty(self.kfold, self.epochs)
        
    def five_fold_val(self):
        from sklearn.metrics import accuracy_score
        from sklearn.model_selection import StratifiedKFold
        from sklearn.metrics import confusion_matrix
        from sklearn.metrics import classification_report
        from sklearn.metrics import matthews_corrcoef
        from sklearn.metrics import roc_auc_score
        '''五折交叉验证'''
        
        skf=StratifiedKFold(n_splits=self.kfold, random_state=66, shuffle=True)
        skf.get_n_splits(n_gram_encode_all,label)
        for train_index,eval_index in skf.split(self.data_x,self.data_y):
            model_kfold = textCNN2().to(init.device)
            writer = SummaryWriter('runs/'+str(self.k))
            example_input = self.data_x.to(init.device)
            writer.add_graph(model_kfold, input_to_model=example_input, verbose=False)
            trainx, evalx = self.data_x[train_index], self.data_x[eval_index]
            trainy, evaly = self.data_y[train_index], self.data_y[eval_index]
            self.len_train = trainx.size(0)
            self.len_eval = evalx.size(0)
            
            train_dataset = CustomDataset(trainx, trainy)
            eval_dataset = CustomDataset(evalx, evaly)
            train_dataloader = torch.utils.data.DataLoader(train_dataset,
                                                           batch_size=init.BATCH_SIZE,
                                                           shuffle=True)
            eval_dataloader = torch.utils.data.DataLoader(eval_dataset,
                                               batch_size=init.BATCH_SIZE,
                                               shuffle=True)
            self.train(model_kfold, train_dataloader, eval_dataloader, writer)
            self.k += 1
        
    def train(self, model, train_dataloader, eval_dataloader, writer):
        model.train()
        criterion = nn.CrossEntropyLoss().to(init.device)
        optimizer = torch.optim.Adam(model.parameters(),lr=1e-4)

        for epoch in range(self.epochs):
            print(epoch)
            all_train_loss = 0
            for batch_x, batch_y in tqdm(train_dataloader):
                batch_x, batch_y = batch_x.to(init.device), batch_y.to(init.device)
                pred = model(batch_x)
                loss = criterion(pred, batch_y)
                all_train_loss += loss
                optimizer.zero_grad()
                loss.backward()
                optimizer.step()
            writer.add_scalar('Loss/train_loss', all_train_loss, global_step=epoch)

            self.evaluate(model, eval_dataloader, writer, epoch)
                
            
    def evaluate(self,model, eval_dataloader, writer, epoch):
        model.eval()
        criterion = nn.CrossEntropyLoss().to(init.device)
        with torch.no_grad():
            all_loss = 0
            all_correct = 0
            
            for batch_x, batch_y in tqdm(eval_dataloader):
                    batch_x, batch_y = batch_x.to(init.device), batch_y.to(init.device)
                    pred = model(batch_x)
                    all_loss += criterion(pred, batch_y)
                    all_correct += (pred.argmax(dim=1)==batch_y).sum()
            cur_acc = all_correct.item()/self.len_eval
            writer.add_scalar('Loss/eval_loss', all_loss, global_step=epoch)
            writer.add_scalar('Eval/eval_acc', cur_acc, global_step=epoch)
            self.log_evalacc[self.k][epoch] = cur_acc
            print(all_loss)
            if cur_acc > self.best_evalscore:
                self.best_evalscore = cur_acc
            print(self.best_evalscore)
        
                    
    def pred(self):
        pass
    

    

In [23]:
trainer = trainer(model, 1000, n_gram_encode_all, label)

In [24]:
# trainer.train(dataloader=dataloader)
trainer.five_fold_val()

0



tensor(3.9825, device='cuda:0')
0.7254901960784313
1



tensor(4.0563, device='cuda:0')
0.7254901960784313
2



tensor(3.9066, device='cuda:0')
0.7254901960784313
3



tensor(3.8746, device='cuda:0')
0.7254901960784313
4


...


tensor(7.2771, device='cuda:0')
0.8719211822660099
996



tensor(7.9212, device='cuda:0')
0.8719211822660099
997



tensor(7.3541, device='cuda:0')
0.8719211822660099
998



tensor(7.6206, device='cuda:0')
0.8719211822660099
999



tensor(8.8130, device='cuda:0')
0.8719211822660099


In [29]:
max(trainer.log_evalacc.mean(dim=0))

tensor(0.8505)